In [1]:
import numpy as np
import pandas as pd

In [2]:
df_dtw = pd.read_csv("../data/df_dtw_comp.csv")

In [3]:
df_dtw.head()

ts_1  no_1  class_1                 ts_2  no_2  class_2  \
0            ArrowHead   153        2            ArrowHead     8        2   
1            ArrowHead   154        2            ArrowHead    17        2   
2  InsectWingbeatSound    98        8  InsectWingbeatSound   175        7   
3  InsectWingbeatSound   174        5  InsectWingbeatSound   170        9   
4  InsectWingbeatSound   194        4  InsectWingbeatSound    61        4   

   min_dtw_dist  
0     11.453478  
1      7.934686  
2     24.418690  
3     32.303582  
4     16.177841

## thoughts

- consider only the ones where the result was found in the same category (because that seems more reasonable to the class)
- check percentage that match vs the ones that  don't

In [4]:
df_dtw_sub = df_dtw[df_dtw['ts_1']==df_dtw['ts_2']]

In [9]:
df_dtw.shape

(1420, 7)

In [10]:
df_dtw_sub.shape

(889, 7)

In [11]:
df_dtw_cls = df_dtw[(df_dtw['ts_1']==df_dtw['ts_2']) &
       (df_dtw['class_1']==df_dtw['class_2'])]

In [12]:
df_dtw_cls

ts_1  no_1  class_1                 ts_2  no_2  class_2  \
0               ArrowHead   153        2            ArrowHead     8        2   
1               ArrowHead   154        2            ArrowHead    17        2   
4     InsectWingbeatSound   194        4  InsectWingbeatSound    61        4   
6     InsectWingbeatSound  1138        1  InsectWingbeatSound   212        1   
8     InsectWingbeatSound  1577        9  InsectWingbeatSound    10        9   
...                   ...   ...      ...                  ...   ...      ...   
1414                PLAID   505        9                PLAID   507        9   
1415                PLAID   511        9                PLAID   513        9   
1417               Mallat    50        6               Mallat    44        6   
1418               Mallat   817        7               Mallat    28        7   
1419               Mallat  1223        1               Mallat    34        1   

      min_dtw_dist  
0        11.453478  
1         7.934686  
4        16.177841  
6        22.607338  
8        25.816940  
...            ...  
1414   1220.501439  
1415     24.602363  
1417     52.752090  
1418     46.783404  
1419     40.734581  

[658 rows x 7 columns]

In [13]:
658/1420

0.46338028169014084

### FFT-based matches

In [14]:
df_fft = pd.read_csv("../data/df_ucr_min_delta.csv")

In [18]:
df_T = df_fft.T

In [22]:
df_T.head(10)

0       1      2         3         4         5         6      \
ts_1         ACSF1   ACSF1  ACSF1     ACSF1     ACSF1     ACSF1     ACSF1   
no_1             0       0      0         0         0         0         0   
class_1          9       9      9         9         9         9         9   
ts_2         ACSF1   ACSF1  ACSF1     ACSF1     ACSF1     ACSF1     ACSF1   
no_2             0      89      6         2         2        40         2   
class_2          0      89      6         2         2        40         2   
type         Welch   Welch  Welch     Welch     Welch     Welch     Welch   
match_score  11001   11001  11001     11001     11001     11001     11001   
min_kpi        d_m  d_mean  d_std     d_q25     d_q50     d_q75     d_min   
value          0.0     0.0    0.0  0.000022  0.000022  0.000563  0.002989   

                7                8                9      ...       27454  \
ts_1            ACSF1            ACSF1            ACSF1  ...        Yoga   
no_1                0                0                0  ...        2690   
class_1             9                9                9  ...           2   
ts_2            ACSF1  ElectricDevices  ElectricDevices  ...  Lightning2   
no_2                9              523             8390  ...          14   
class_2             9              523             8390  ...          14   
type            Welch          Hamming          Hamming  ...         fft   
match_score     11001            11100            11100  ...       11101   
min_kpi         d_max              d_m           d_mean  ...       d_min   
value        0.000233           1364.0              0.0  ...    1.193291   

                  27455  27456   27457  27458     27459     27460     27461  \
ts_1               Yoga   Yoga    Yoga   Yoga      Yoga      Yoga      Yoga   
no_1               2690   2690    2690   2690      2690      2690      2690   
class_1               2      2       2      2         2         2         2   
ts_2         Lightning2   Yoga    Yoga   Yoga      Yoga   OSULeaf   OSULeaf   
no_2                 14     41     298    251       220        76        61   
class_2              14     41     298    251       220        76        61   
type                fft  Welch   Welch  Welch     Welch     Welch     Welch   
match_score       11101  11111   11111  11111     11111     11111     11111   
min_kpi           d_max    d_m  d_mean  d_std     d_q25     d_q50     d_q75   
value         17.385595    0.0     0.0    0.0  0.001505  0.000186  0.001221   

                27462     27463  
ts_1             Yoga      Yoga  
no_1             2690      2690  
class_1             2         2  
ts_2             Yoga      Yoga  
no_2               64       250  
class_2            64       250  
type            Welch     Welch  
match_score     11111     11111  
min_kpi         d_min     d_max  
value        0.007975  0.000541  

[10 rows x 27464 columns]

In [25]:
fft_types = df_fft['type'].unique()
kpis = df_fft['min_kpi'].unique()
print(f"FFT types: {fft_types}")
print(f"KPIs: {kpis}")

FFT types: ['Welch' 'Hamming' 'fft']
KPIs: ['d_m' 'd_mean' 'd_std' 'd_q25' 'd_q50' 'd_q75' 'd_min' 'd_max']


In [26]:
df_fft_res  = df_fft[(df_fft['ts_1']==df_fft['ts_2'])&
       (df_fft['class_1']==df_fft['class_2'])]

In [29]:
df_fft_res.groupby(['type','min_kpi']).count()

ts_1  no_1  class_1  ts_2  no_2  class_2  match_score  value
type    min_kpi                                                              
Hamming d_m         4     4        4     4     4        4            4      4
        d_max       3     3        3     3     3        3            3      3
        d_mean      3     3        3     3     3        3            3      3
        d_min       5     5        5     5     5        5            5      5
        d_q25       3     3        3     3     3        3            3      3
        d_q50       3     3        3     3     3        3            3      3
        d_q75       3     3        3     3     3        3            3      3
        d_std       4     4        4     4     4        4            4      4
Welch   d_m        39    39       39    39    39       39           39     39
        d_max       9     9        9     9     9        9            9      9
        d_mean      4     4        4     4     4        4            4      4
        d_min       7     7        7     7     7        7            7      7
        d_q25       5     5        5     5     5        5            5      5
        d_q50       5     5        5     5     5        5            5      5
        d_q75       6     6        6     6     6        6            6      6
        d_std      12    12       12    12    12       12           12     12
fft     d_m         4     4        4     4     4        4            4      4
        d_max       1     1        1     1     1        1            1      1
        d_std       1     1        1     1     1        1            1      1

In [ ]:
def find_matches(df: pd.DataFrame) -> pd.DataFrame:
    """return only matching classes"""
    df_res  = df[(df['ts_1']==df['ts_2'])&
       (df['class_1']==df['class_2'])]
    